# Modelling and testing stem cell populations with F# #

## Introduction

Stem cells maintain the structure of tissues and organs in the body. How they grow and divide is a subject of intensive study, but one concept has been explored heavily over the past decade and found to describe how the stem cell population is maintained in many different tissues.  In this tutorial we will give concrete examples of how to build simulators that explore how changing one part of the model alters cell growth, and compare the model behaviour against experimental data.

![Schematic of single progenitor model](Cartoon.png)

In this tutorial we are going to explore one part of the single progenitor model (depicted above). The model has two types of cell; stem cells and differentiated cells. Stem cells divide to give two daughter cells, which can either be one stem cell and one differentiated cell (asymmetric division), both stem cells, or both differentiated cells (symmetric division). As the population of stem cells is constant, the probability of both possible symmetric divisions is equal, so over time, on average, one stem cell gives one differentiated cell and one stem cell.

In the past the division (sometimes written as $\lambda$) and stratification (sometimes written as $\Gamma$) times have been modelled as following an exponential distribution. Recent experiments have suggested that this is inappropriate and may bias our analysis. Here we will build simulators that use more complex distributions and see how they change the model behaviour by both direct comparison with experimental data and by exploring the general properties.

This document has a parallel document written in python, performing the same functions using appropriate python modules. Where sensible functions with the same task have the same name. By referring to both of them you can see how similar tasks can be accomplished in both languages.

### Background biology

Whilst this tutorial has been written to focus on aspects of the maths and programming, the code and text necessarily use a few technical terms. This section introduces some of them and how they are used here.

A *cell* is the basic unit of living matter- it eats, divides, dies, and carries out functions specific to the tissue its in. The cell *fate* is the cells function, and in this model is determined on birth. This dictates what that cell can go on to do in the future. In this model, one cell fate is to be a *stem cell*. Stem cells will go on to divide at some point in the future. The *cell cycle* is the process that immediate proceeds division. This is expected to last an average length of time for a given cell type, but the distribution of times is not necessarily known. The alternative cell fate in this model is to *differentiate*; in this case the cell will stop dividing, and eventually leave the space that stem cells occupy by a process called *stratification*. 

A *clone* is the set of descendants from a single cell at a specific point in time. These could be defined by a natural event- such as a mutation- or a result of an experiment. A common experiment known as *lineage tracing* is to monitor the size of clones in growing tissues is to add an *inheritable*, permenant coloured label to cells at a specific timepoint. As the label is inheritable all of the cells in a clone will carry it, and can be distinguished and counted under a microscope.

Another type of labelling experiment involves the use of a *histone* label. This label is switched on during the experiment similar to lineage tracing. However, the labelled histone stops being produced after the experiment is started, though cells continue to produce unlabelled histones. This means that every time the cell divides the amount of label halves, allowing cell divisions to be tracked over time.

## Plan and constraints

In this document we will present code to do 4 different tasks:

1. Simulate cell fates to show how clones compete neutrally to dominate the tissue
2. Take the results of those simulations and study the effect of different cell-cycle time distributions by generating random numbers taken from different distributions.
3. Simulate an experiment where a label becomes more dilute every time a cell divides
4. Use this simulator with an ''Approximate Bayesian Computation'' based analysis to find out which distribution best describes some collected data.

In doing so we will look to report and plot data as a we go along to confirm that different parts of the code are working. Wherever possible we use external libraries to perform calculations rather than reimplement the functions.

We also specify a seed for random number generation for calculations. This is to help ensure repeatability.

## Machine variables

These variables are referenced by the code below and are machine specific- *you need to alter these for some functions to work!* 

The comments indicate what they should be set to and what they are used for.

In [1]:
//This is where your python 3.5 install is.
//Macports on a mac may install it at /opt/local/Library/Frameworks/Python.framework/Versions/3.5/
let pythonPath = @"C:\Users\bh418\AppData\Local\Programs\Python\Python35\"
//This is where your notebook is. This cannot be found automatically and is needed to find the supplied experimental data
let dataLocation= @"C:/Users/bh418/Notebook/SP Sim/"



## Load external libraries

We use plotly for graphs, MathNet and Accord for statistical functions and random distributiosn, pythnonnet (and FSharp.Interop,Dynamic) for comparing with python functions.

In [2]:
open System
#load "XPlot.Plotly.Paket.fsx"
#load "XPlot.Plotly.fsx"
open XPlot.Plotly

In [3]:
#load "Paket.fsx"
Paket.Package
  [ "MathNet.Numerics"
    "MathNet.Numerics.FSharp"
    "FSharp.Data"
    "Accord"
    "Accord.Statistics"
    "Accord.Math"
    "pythonnet"
    "FSharp.Interop.Dynamic"
  ]
#load "Paket.Generated.Refs.fsx"
open Python.Runtime
open FSharp.Interop.Dynamic
open System.Collections.Generic

//Set a few additional variables that depend on both libraries being loaded and machine specific variables
let pythonLib = pythonPath + @"\lib"
let path' = pythonPath + ";" + Environment.GetEnvironmentVariable("PATH")
Environment.SetEnvironmentVariable("PATH", path')
Environment.SetEnvironmentVariable("PYTHONHOME", pythonPath)
Environment.SetEnvironmentVariable("PYTHONPATH ", pythonLib)

## Benchmark and utility functions 

timeIt and timeStore both are used for measuring how much absolute and CPU time functions take. timeIt works by timing a specific function, whilst, timeStore is intended to be used by modified functions that can be passed a reference. These modified functions can be used to sum the total time spent in, for example, a single line of a function run multiple times.

gensym is a function that generates a new number everytime its run, by storing and incrementing a reference variable. This is used in the code to ensure that unique seeds are used for random number generation.

In [4]:
let timeIt f =
   let proc = System.Diagnostics.Process.GetCurrentProcess()
   let stopWatch = System.Diagnostics.Stopwatch.StartNew()
   let t = proc.TotalProcessorTime
   let result = f ()
   let dt = proc.TotalProcessorTime-t
   stopWatch.Stop()
   printfn "Wall: %fms CPU: %fms" stopWatch.Elapsed.TotalMilliseconds dt.TotalMilliseconds
   result

let timeStore r f =
  let proc = System.Diagnostics.Process.GetCurrentProcess()
  let stopWatch = System.Diagnostics.Stopwatch.StartNew()
  let result = f ()
  stopWatch.Stop()
  r := !r + stopWatch.Elapsed.TotalMilliseconds
  result

let gensym =
    let x = ref 0
    fun () ->
        let result = !x
        incr x
        result

## Using SciPy in F# #

Below is a function that wraps the use of a specific function from scipy which was found to be substantially faster than the equivalent in accord (the calculation of the KS test statistic). This relies on pythonpath being set correctly above, and scipy and numpy having been installed.

In [5]:
let (scipyKS: float [] -> float [] -> float)  =
    let SeqToPyFloat ( aSeq : float seq ) =
            let list = new Python.Runtime.PyList()
            aSeq |> Seq.iter( fun x -> list.Append( new PyFloat(x)))
            list
    PythonEngine.Initialize()
    ignore <| PythonEngine.BeginAllowThreads()
    fun a b ->
        //use gil = Py.GIL()
        let token = PythonEngine.AcquireLock ()
        let spstats = Py.Import("scipy.stats")
        let np = Py.Import("numpy")
        let npa = np?array( a  |> SeqToPyFloat )
        let npb = np?array( b  |> SeqToPyFloat )
        let r = spstats?ks_2samp(npa,npb)
        let result = r?statistic?item() : float
        PythonEngine.ReleaseLock token
        
        result

# Simulating cell fates

![Dendrograms of cell fates](CellFate.png)

The first behaviour we will simulate is fate determination of cells in a clone, starting from a single cell. This is the pattern of changing cell states as cells go on to divide. Examples of cell fates are drawn as dendrograms above. In (A), A cell divides, but neither daughter cell is a stem cell and so division stops. In (B), the divisions form a more complex (and unfinished pattern)- in the first division the cell fates are asymmetric giving one stem cell and one differentiated cell. That stem cell divides to give two stem cells, and so on until either all daughter cells in the clone divide becoming differentiated cells, or we stop the experiment

In this specific situation we are only simulating the fates- that is to say, we know that division and stratification occur at different rates, but we are not taking account of that yet- we just record the order in which things happened in discrete time. Even without precise timings we expect the functions to give us some of the key properties of the clone growth. 

We define a clone through a record type, where we record when the clone was born (*birthtime*), when the cell left the clone (*lifeTime*), the random number generator used to determine the next fate (*rng*), whether the cell is a stem cell (*stem*) and the probability of dividing to give daughters with the same cell fate (*r*). We also include a list of other clones that the clone has given birth to (*sibling*), and an integer used to assign a unique identity to every cell created (*identity*). Note we have defined other elements in the record, which we use in future.

The function *fateSimulate* simulates the life of a single cell. Given a clone record, a maximum number of divisions (*limit*), and a reference variable used to track unique identities (*idTrack*) it loops through events in the cells life, giving a final clone with some variables changed. 

In each loop fateSimulate first tests whether the cell has been simulated enough times, and if it has returning a modified version of the last state of the cell. This is either the last state with the lifetime set to the current time (and a Boolean variable, *survivor*, set to true to indicate this), or if the cell is not a stem cell at the end of the simulation, the last state with the lifetime set to the current time+1. 

Next, if the cell is still a stem cell, it creates a new daughter cell as a copy of the parent, with a new unique identity value. We then determine using r and a random number whether the daughter and parent are stem cells after division, defining a new cell to replace the parent and the daughter. Finally, we restart the loop using the replacement cell with the daughter added to the list of siblings.

This however is not sufficient- we want to simulate all the daugter cells as well to see how the clone grows. To do this we define a recursive function *cloneSimulateInternal*, which simulates a single cell, then recursively runs on all of the daughter cells (and their daughter cells and so on), appending only the key information as a tuple to list reference. This function itself is run through *cloneSimulate*, which sorts the final list by unique identifier (this is important for later functions).

Finally, the function *experiment* is defined which takes a list of discrete timepoints, runs cloneSimulate, and asks how many cells are alive at each time.

In [6]:
type clone = { 
                parent:    int
                identity:  int
                birthTime: int
                lifeTime:  int
                rng:       System.Random
                survivor:  bool
                r:         float 
                stem:      bool
                sibling  : clone list
                }

let fateSimulate limit (c:clone) idTrack =
    let rec simulate limit (c:clone) time =
        //printf "Time %d\n" time
        if (time>limit) then 
            //printf "Finished- out of time\n"
            if c.stem then 
                {c with survivor=true; lifeTime=time; sibling=(c.sibling)} 
            else 
                {c with lifeTime=time+1; sibling=(c.sibling)}
        else    
            if c.stem then 
                let rand = c.rng.NextDouble()
                let time' = time + 1
                let (c',sibling) =  idTrack := !idTrack+1
                                    if (rand < c.r) then 
                                        //printf "AA @ %d\n" time
                                        (c,{c with parent=c.identity;
                                                    identity= !idTrack;
                                                    birthTime=time';
                                                    sibling=[]})
                                    elif (rand < 2.*c.r) then 
                                        //printf "BB @ %d\n" time
                                        ({c with stem=false},{c with parent=c.identity;
                                                                        identity= !idTrack;
                                                                        stem=false; 
                                                                        birthTime=time';
                                                                        sibling=[]})
                                    else
                                        //printf "AB @ %d\n" time
                                        (c,{c with parent=c.identity;
                                                    identity= !idTrack;
                                                    stem=false; 
                                                    birthTime=time';
                                                    sibling=[]})
                simulate limit {c' with sibling=(sibling::c.sibling)} (time') 
            else 
                {c with lifeTime=time+1; sibling=(c.sibling)}
        
    simulate limit c c.birthTime
    
let rec cloneSimulateInternal limit c acc idTrack = 
    let c' = fateSimulate limit c idTrack
    acc := (c'.birthTime,c'.lifeTime,c'.survivor,c'.parent,c'.identity)::!acc
    for d in c'.sibling do
        cloneSimulateInternal limit d acc idTrack
    ()
    
let cloneSimulate limit c =
    let result = ref []
    cloneSimulateInternal limit c result (ref 0)
    //Ordering by creation helps generate times later
    !result |> Array.ofList |> Array.sortBy (fun (_,_,_,_,i) -> i) |> Array.map (fun (b,l,s,p,_) -> (b,l,s,p) )
    
let experiment c timePoints =
    let limit = List.max timePoints
    let lifespans = cloneSimulate limit c 
    let within a b c =
        if c>a && c<=b then
            1
        else
            0
    List.map (fun t -> Array.fold (fun acc  (b,d,_,_) -> acc + (within b d t) )  0 lifespans ) timePoints
    |> Array.ofList
    //[sum([within(b,d,t) for (b,d,_,_) in lifespans]) for t in timePoints]
    

## Testing the simulator

Below we can run a few tests. We initially define a cell and run a simulation just of that. We go on to simulate a clone, and an experiment to see if the functions run and generate sensible outputs. 

We finish with a simulation of 10000 clones, timing the calculation. As the most easily measurable properties of the model are the averages, we will use this for generating some plots. To ensure that our random numbers are really random we can look at a couple of elements in the array and compare them.

In [7]:
let symClone = { 
                sibling=[]
                birthTime=0
                lifeTime=0
                rng= new System.Random(1982)
                survivor=false
                stem=true
                r=0.25
                parent=(-1)
                identity=0
                }
                
fateSimulate 1 symClone (ref 0)


{parent = -1;
 identity = 0;
 birthTime = 0;
 lifeTime = 3;
 rng = System.Random;
 survivor = false;
 r = 0.25;
 stem = false;
 sibling = [{parent = 0;
             identity = 2;
             birthTime = 2;
             lifeTime = 0;
             rng = System.Random;
             survivor = false;
             r = 0.25;
             stem = false;
             sibling = [];}; {parent = 0;
                              identity = 1;
                              birthTime = 1;
                              lifeTime = 0;
                              rng = System.Random;
                              survivor = false;
                              r = 0.25;
                              stem = true;
                              sibling = [];}];}

In [8]:
let r = cloneSimulate 10 symClone 
r

[|(0, 10, false, -1); (1, 6, false, 0); (2, 3, false, 0); (3, 7, false, 0);
  (4, 5, false, 0); (5, 6, false, 0); (6, 7, false, 0); (7, 12, false, 0);
  (8, 11, true, 0); (9, 10, false, 0); (9, 10, false, 8); (10, 12, false, 8);
  (11, 12, false, 8); (11, 12, false, 11); (8, 9, false, 7); (9, 11, true, 7);
  (10, 11, false, 7); (11, 12, false, 7); (10, 11, false, 15);
  (11, 11, true, 15); (4, 7, false, 3); (5, 6, false, 3); (6, 7, false, 3);
  (5, 6, false, 20); (6, 7, false, 20); (2, 3, false, 1); (3, 4, false, 1);
  (4, 8, false, 1); (5, 6, false, 1); (5, 6, false, 27); (6, 7, false, 27);
  (7, 8, false, 27)|]

In [9]:
let exp = experiment symClone [0;1;3;6;12;36;52]
exp

[|0; 1; 2; 2; 6; 12; 10|]

In [10]:
let lots = timeIt (fun _ -> Array.init 10000 (fun seed -> cloneSimulate 100 {symClone with rng=new System.Random(seed)} ) )


Wall: 262.123500ms CPU: 265.625000ms


In [11]:
lots.[0]

[|(0, 9, false, -1); (1, 2, false, 0); (2, 3, false, 0); (3, 4, false, 0);
  (4, 5, false, 0); (5, 8, false, 0); (6, 7, false, 0); (7, 8, false, 0);
  (8, 9, false, 0); (6, 7, false, 5); (7, 8, false, 5)|]

In [12]:
lots.[(Array.length lots) - 1]

[|(0, 2, false, -1); (1, 2, false, 0)|]

## Properties of a collection of clones

Lets run some experiments in a similar way to the code above, and check the properties. 

The model represents homeostasis, so we expect that there should be roughly 20000 cells at each timepoint, which we can check by summing for all elements. 

We also expect the average surviving clone size to increase linearly over time with a slope of ~0.5. This can be seen by calculating and plotting this using plotly.

Finally, the number of surviving clones should drop over time following a power law- again we can plot and check this using Plotly.

In [13]:
let example = Array.init 10000 (fun seed -> experiment {symClone with rng=new System.Random(seed)} [2;3;6;12;36;52;104])


In [14]:
example

[|[|2; 2; 2; 0; 0; 0; 0|]; [|2; 4; 2; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|];
  [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|];
  [|2; 2; 2; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|];
  [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 2; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|];
  [|2; 2; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|]; [|2; 4; 2; 0; 0; 0; 0|];
  [|2; 2; 2; 0; 0; 0; 0|]; [|2; 4; 4; 4; 0; 0; 0|]; [|2; 2; 4; 2; 0; 0; 0|];
  [|2; 4; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|]; [|2; 4; 10; 6; 0; 0; 0|];
  [|2; 2; 0; 0; 0; 0; 0|]; [|2; 4; 4; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|];
  [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 4; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|];
  [|2; 2; 0; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|];
  [|2; 0; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|];
  [|2; 2; 2; 4; 0; 0; 0|]; [|2; 0; 0; 0; 0; 0; 0|];
  [|2; 4; 10; 18; 82; 110; 70|]; [|2; 2; 0; 0; 0; 0; 0|];
  [|2; 4; 0; 0; 0; 0; 0|]; [|2; 2; 0; 0; 0

In [15]:
Array.fold (fun acc c -> Array.map2 (fun a' c' -> a'+c') acc c ) [|0;0;0;0;0;0;0|] example

[|20000; 19990; 20192; 19928; 19936; 20678; 19190|]

In [16]:
Array.fold (fun acc c -> Array.map2 (fun a' c' -> if c' > 0 then a'+ 1 else a') acc c ) [|0;0;0;0;0;0;0|] example

[|10000; 7497; 4502; 2583; 987; 727; 362|]

In [17]:
let survivors = Array.fold (fun acc c -> Array.map2 (fun a' c' -> if c' > 0 then a'+ 1 else a') acc c ) [|0;0;0;0;0;0;0|] example
let cells = Array.fold (fun acc c -> Array.map2 (fun a' c' -> a'+c') acc c ) [|0;0;0;0;0;0;0|] example
let mean = Array.map2 (fun c s -> float(c)/float(s)) cells survivors
mean

[|2.0; 2.666399893; 4.485117725; 7.715060008; 20.19858156; 28.44291609;
  53.01104972|]

In [18]:
let smooth = Scatter(
                        x = [2;3;6;12;36;52;104],
                        y = List.ofArray mean,
                        mode = "line"
                    ) 
[smooth]
|> Chart.Plot

XPlot.Plotly.PlotlyChart

In [19]:
let surv = Scatter(
                        x = [2;3;6;12;36;52;104],
                        y = List.ofArray survivors,
                        mode = "line"
                    ) 
[surv]
|> Chart.Plot

XPlot.Plotly.PlotlyChart

# Converting clone lifespan to realistic times

The fate simulator is able to generate the orders of events in a clones lifetime, but in order to compare this with experimental data we need to use the outputs from that function, and transform them into floating point numbers that reflect the division and stratification rates. The most common way to do this is to draw the division times from an exponential distribution characterised by its mean, but we also know that the exponential distribution is unrealistic for cell division times. Here we explore two alternative distributions used in the literature; a short, deterministic delay (the delay or refractory period) followed by an exponential distribution, and a deterministic lag period followed by times selected from a gamma distribution (with an additional shape parameter). As the exponential distribution is a special case of the gamma distribution where the shape is 1., we can focus on using just the gamma distribution when we start to compare with experimental data.

We first define functions that allow us to set create a random number generator for a given distribution with a specific set of parameters (using the MathNet library to generate the underlying distribution). In each case the overall mean time for events to occur and a random number generator is passed to the function. In addition to this, a delay may be passed (either as an absolute delay, or expressed as a fraction of the mean) and a shape parameter. In each case the object returned is a function that takes unit as an input and returns a new floating point number from the distribution.

Note that in the python implementation we preallocate random numbers for speed; this has no advantage here so we don't bother.

In [20]:
[<Measure>]
type day

[<Measure>]
type week

let dayToWeek d = 1.<week>*d/7.<day>

let weekToDay w = 7.<day>/1.<week>

let exponential mean rng =
    let scale = 1.<day>/mean
    fun _ -> MathNet.Numerics.Distributions.Exponential.Sample(rng, scale)*1.<day> //accepts a rate
    
let exponentialDelay delay mean rng = 
    let scale = 1.<day>/(mean-delay)
    fun _ -> delay + MathNet.Numerics.Distributions.Exponential.Sample(rng, scale)*1.<day> //accepts a rate

let exponentialFracDelay fracDelay mean rng = 
    //Expressing the delay as a fraction of the mean might be a better way..
    let delay = mean*fracDelay
    exponentialDelay delay mean rng
    
let gamma mean shape rng =
    let invscale = 1.<day>*shape/mean
    fun _ -> MathNet.Numerics.Distributions.Gamma.Sample(rng, shape, invscale)*1.<day>
    
let gammaDelay delay mean shape rng = 
    let gFunc = gamma (mean-delay) shape rng
    fun _ -> delay + (gFunc ()) 

let gammaFracDelay fracDelay mean shape rng = 
    //Expressing the delay as a fraction of the mean might be a better way..
    let delay = mean*fracDelay
    gammaDelay delay mean shape rng

## Converting discrete time to real time

The function *correctMap* below takes two rate functions (of the type we have just defined above), an initial time, and an array of tuples generated by the cloneSimulate function defined above. It returns a new array with the time of birth and the time of loss of the cell. 

To do this we first generate an array with random numbers drawn from the function representing the division times. If the cell stratifies we replace the last number in the array with a value drawn from the function representing stratification times. Finally, we perform a cumulative sum so that all elements represent the times taken for each event to happen from an initial timepoint (here arbitrarily set to zero).

This gives us a series of timepoints that are accurate relative to the time when the cell was first born. However, we need the times to be relative to the start of the experiment to be useful. To do this for each cell we need to look at the times of its parent (and in turn, its parents and grandparents until the original cell) and adjust all the timepoints by the time the cell was born. Uniquely, the original cell has a parent set to a negative value and if this is found in the loop, the initial time is set to the value passed when calling the function.

As an example, we want to generate times for the third cell in a clone. The third cell is a daughter of the first. The discrete times are 

cell 1 born @ 0, lost @ 3
cell 3 born @ 1, lost @ 2

This will give us initially two arrays of timepoints;

cell1 = [|0.;0.5;1.0;1.5;|]
cell3 = [|0.;1.0|]

For cell 3, assuming that the initial time of the experiment was 0 (so cell 1 remains unchanged), we then need to add 0.5 (the first time from cell 1) to every timepoint. We get this by using the discrete birthtime as an index in the array. Finally, we return the first and last elements of the new array as the time of birth and the time of death; 0.5 and 1.5.

This relies on being able to look up the parent time. Earlier we sorted the array returned by cloneSimulate by the unique identifier- this allows us to use the parent id (stored in the tuple) as an index in the original search. It also ensures that we correct the times in order of cell creation- this is important as when we correct the times we mutate the values in the original array, and ensures that we have always corrected the parents before we update their children. 

We now have enough information to directly compare our results with lineage tracing data.

In [21]:
let timeMap divisionFunc stratificationFunc t =
    let b,d,s,p = t
    Array.init (d-b) (fun _ -> divisionFunc () )
    //replace the last value to represent stratification
    |> fun x -> if s then 
                    x 
                else 
                    x.[((Array.length x)-1)] <- stratificationFunc ()
                    x 
    |> Array.scan (fun acc e -> acc+e) 0.<day> 

let birthTime initial (times: float<day> [] []) (cloneRegister: (int*int*bool*int) array) c t = 
    let (birthday,d,s,p) = c
    let timeOnBirth = if p < 0 then 
                            initial 
                        else 
                            let parentBirthday,_,_,_ = cloneRegister.[p]
                            times.[p].[birthday-parentBirthday]
    

    //Add the time on birth to every element of t (through mutation)
    //This is important as it ensures that cells that refer to this time pick up the right time
    for i in [0..((Array.length t)-1)] do
        t.[i] <- t.[i]+timeOnBirth
    //Finally return an array of the birth and death times
    if ((Array.length t) = 0) then 
        [|timeOnBirth;infinity*1.<day>|]
    else
        [|timeOnBirth;t.[(Array.length t)-1]|]

let correctTime initial divisionFunc stratificationFunc cloneRegister =
    let times = Array.map (timeMap divisionFunc stratificationFunc) cloneRegister
    //Now correct the times based on parents times
    Array.map2 (birthTime initial times cloneRegister) cloneRegister times
    

## Testing functions

Here we demonstrate how different functions we've defined work. We explore the random number generators, then test elements of the large array of clone simulations we defined above (called *lots*), before applying the function to all elements and timing it.

In [22]:
let rng = System.Random(2001)
let div' = gamma 0.01<day> 1. rng
for i in 0..10 do
    printf "%f\n" (div' ()) 

0.002379
0.000339
0.007630
0.014094
0.017674
0.010000
0.014934
0.010485
0.007039
0.001875
0.004806


In [23]:
let div = gammaFracDelay 0.5 2.<day> 8. rng
for i in 0..10 do
    printf "%f\n" (div ()) 
    

2.083200
2.301327
1.831888
2.005631
2.192347
1.933288
1.902485
1.313540
2.119571
2.178604
1.766931


In [24]:
List.sum(List.init 1000000 (fun _ -> div ())) //This tests that the function givesthe right times- if the mean is 2, the sum should be 2M

1999618.025

In [25]:
let strat = exponential 2.<day> rng
List.sum(List.init 1000000 (fun _ -> strat ())) //This tests that the function givesthe right times- if the mean is 2, the sum should be 2M

1998607.196

In [26]:
let test = lots.[0]
correctTime  0.<day> div div test

[|[|0.0; 17.06139003|]; [|1.563776103; 3.570926102|]; [|3.3297912; 5.136533725|];
  [|5.233165134; 7.162271437|]; [|6.953836426; 8.862950243|];
  [|8.413133527; 14.36476424|]; [|10.40907995; 13.18831093|];
  [|12.43207865; 14.15021746|]; [|14.86922274; 17.30675898|];
  [|10.29364268; 12.86507446|]; [|11.85705073; 13.50587231|]|]

In [27]:
test

[|(0, 9, false, -1); (1, 2, false, 0); (2, 3, false, 0); (3, 4, false, 0);
  (4, 5, false, 0); (5, 8, false, 0); (6, 7, false, 0); (7, 8, false, 0);
  (8, 9, false, 0); (6, 7, false, 5); (7, 8, false, 5)|]

In [28]:
let times = Array.map (timeMap div div) test
times

[|[|0.0; 2.414048153; 3.994125617; 6.114416452; 8.566918141; 10.36066441;
    11.84514039; 14.19735431; 15.75032437; 17.34316784|]; [|0.0; 1.651608694|];
  [|0.0; 1.670608597|]; [|0.0; 2.647588482|]; [|0.0; 1.834594581|];
  [|0.0; 2.46305439; 4.297512731; 6.049688126|]; [|0.0; 1.897089578|];
  [|0.0; 2.078069097|]; [|0.0; 1.507219744|]; [|0.0; 2.017038986|];
  [|0.0; 3.184336399|]|]

In [29]:
let t' = timeIt (fun _ -> (Array.map (correctTime 0.<day> div div) lots) )


Wall: 859.508400ms CPU: 796.875000ms


In [30]:
t'

[|[|[|0.0; 18.02879706|]; [|1.817534017; 3.83575531|];
    [|4.113552825; 5.997524049|]; [|6.879085077; 8.982624295|];
    [|8.937543927; 10.78975953|]; [|10.87735523; 16.31870445|];
    [|12.96805546; 14.95031034|]; [|14.9189193; 17.22046403|];
    [|16.44851363; 18.10652608|]; [|13.16228625; 15.1624055|];
    [|14.61018096; 17.00436678|]|];
  [|[|0.0; 7.55147192|]; [|1.657084152; 5.128199367|];
    [|3.931984773; 11.88730022|]; [|5.834612801; 7.720019289|];
    [|5.881666052; 8.507972531|]; [|8.075284957; 9.889161116|];
    [|9.882332704; 11.5298778|]; [|3.362141576; 5.037337912|]|];
  [|[|0.0; 5.107378953|]; [|1.598149602; 3.532301088|];
    [|3.220284891; 5.392350588|]|];
  [|[|0.0; 3.2632558|]; [|1.397574134; 3.584787298|]|];
  [|[|0.0; 10.21201667|]; [|1.995538477; 4.591313061|];
    [|4.074035184; 6.087204595|]; [|6.049488314; 8.481702025|];
    [|8.161761947; 9.905569408|]|];
  [|[|0.0; 3.95514723|]; [|2.031358979; 3.60503624|]|];
  [|[|0.0; 18.14414991|]; [|2.325990831; 4.2186

## Comparing models with experiments

Here we will take the simulators we have created and use them to search an experimental dataset for parameters that describe the model well. We will take some published data of measured clone sizes, make a plot to show that it has some of the expected properties (specifically, linearly increasing average clone size over time). We will then use a set of simulations to estimate the likelihoods of different parameter combinations for models, and identify the most likely combination by plotting the results as a heatmap. 

To interpret the heatmaps, the parameter combinations with the highest likelihood are the best fitting. For this dataset, we can see that for both exponential and gamma distributions we find low values of $r$ and high values of $\rho$ best describe the data. We can further see that the choice of distribution makes subtle differences on the long term distributions.

We additionally define a function *transpose* which is useful for manipulating non-jagged arrays of arrays.

In [31]:
                               
let transpose (a: 'a [] []) = 
    let x,y = ((Array.length a), (Array.length a.[0]))
    Array.init y (fun yi -> Array.init x (fun xi -> a.[xi].[yi]))

transpose [|[|1;1|];[|2;2|];[|3;3|];|]

[|[|1; 2; 3|]; [|1; 2; 3|]|]

In [32]:
type lineageTracing = {
timePoints: float<day> []
cloneCounts: int [] []
frequency : float [] []
}

//load data
let lineageData = 
    let raw = FSharp.Data.CsvFile.Load(dataLocation+"DoupeAggregate.tsv")
    let contents = raw.Rows |> Array.ofSeq // |> Array.map (fun r -> r.ToString())
    let nrows = Array.length contents
    let ncol = raw.NumberOfColumns
    let counts = Array.init (ncol-1) (fun c -> Array.init nrows (fun r -> int contents.[r].[c+1] ) )
    let freq  = Array.map (fun tp -> let totalClones = (Array.sum tp|>float) 
                                     Array.map (fun count -> (float count)/totalClones ) tp
                                        ) counts
    let times = raw.Headers 
                |> fun s -> match s with 
                            | None -> failwith ""
                            | Some(e) -> e
                |> fun a -> Array.init ((Array.length a)-1) (fun i -> 1.<day>*float(a.[i+1]) )
    {timePoints=times;cloneCounts=counts;frequency=freq}
    

In [33]:
lineageData

{timePoints = [|3.0; 10.0; 21.0; 42.0; 84.0; 180.0; 365.0|];
 cloneCounts =
  [|[|90; 43; 4; 3; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; ...|];
    [|96; 102; 34; 15; 4; 2; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; ...|];
    [|140; 79; 38; 25; 11; 4; 1; 1; 0; 0; 1; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;
      0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0; 0;


### Exploring the data

We showed that the simulations showed a linear growth in average clone size over time. Here we repeat the test on the experimental data.

In [34]:
//Plot average clone size
let averageSize = lineageData.cloneCounts
                    |> Array.map (fun c ->  let cells = Array.mapi (fun i e -> i*e)  c |> Array.sum |> float
                                            let clones =Array.sum c |> float
                                            cells/clones
                                            )
                    |> Array.map2 (fun t n -> (t,n)) lineageData.timePoints
averageSize
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Average clone size over time" ) )
|> Chart.WithLabels ["Experiment"; "Exponential"; "Gamma with delay"]

XPlot.Plotly.PlotlyChart

In [35]:
let likeliHoodCalculation (lineageExperiment: lineageTracing) cloneTimes =
    //1. create clone size frequencies per timepoint from cloneTimes
    let within time (birthDeath: float<day> []) =
        if time >= birthDeath.[0] && time < birthDeath.[1] then 1 else 0
    //For each timepoint, establish the size of each simulated clone at that time. 
    //This is done by adding the number of cells in each clone who are alive (born before and died after) at the timepoint
    let cloneSizes = Array.map (fun t -> 
                                    Array.map (fun clone -> Array.map (within t) clone |> Array.sum ) cloneTimes 
                                    ) lineageExperiment.timePoints
    let maxClone = Array.map Array.max cloneSizes |> Array.max
    let countToArray max c =
        let counts = Array.countBy id c
                     |> Map.ofArray
        Array.init max (fun size ->  match (Map.tryFind (size+1) counts) with
                                     | None -> 0
                                     | Some(s) -> s )

    let cloneCounts = Array.map (countToArray maxClone) cloneSizes
    
    let logfreq = Array.map (fun tp ->   let totalClones = (Array.sum tp|>float) 
                                         //printf "Totalcount = %f\n" totalClones
                                         Array.map (fun count -> (float count)/totalClones |> Math.Log10 ) tp
                                            ) cloneCounts
    //2. Use the frequency from the simulations as probabilities and calculate the log likelihood 
    let mutable sum = 0.
    let mutable missing = 0
    //Find the largest clone size from both sets of data and pick the smallest as the limit
    let maxCloneSize = 
        let exp = (Array.length lineageExperiment.cloneCounts.[0] )-1
        let sim = (Array.length logfreq.[0] )-1
        if exp > sim then sim else exp
    
    for i=0 to maxCloneSize do 
        for t=0 to ((Array.length lineageExperiment.timePoints)-1) do
            //printf "%d,%d -> \n" i t
            //printf "NoFreq %d\n" <| Array.length logfreq.[t]
            let result =    if Double.IsInfinity(logfreq.[t].[i]) then
                                if lineageExperiment.cloneCounts.[t].[i] > 0 then missing <- missing + 1
                                0.
                            else logfreq.[t].[i]*float(lineageExperiment.cloneCounts.[t].[i])
            //probability can be a NaN- if there are counts which haven't been sampled. We count/filter
            //printf "\t%f (%f*%d)\n" result logfreq.[t].[i] lineageExperiment.cloneCounts.[t].[i]
            sum <- sum + result
    //report how often we miss a count
    //printf "%d missing probabilities\n" missing
    sum

In [36]:
type gridResult = {
    logLikelihood : float [] []
    rho : float []
    r : float []
}

let gridSearch rBins rhoBins (meanDivTime: float<day>) divF data =
    let sampleSize = 10000
    let rVals = Array.init rBins (fun i -> float(i)*0.5/float(rBins) + 0.25/float(rBins) )
    let rhoVals = Array.init rBins (fun i -> float(i)*1./float(rhoBins) + 0.5/float(rhoBins) )

    let massSimulation rhoAll r =
        let genSeed =
            let seed = ref 0
            fun _ ->
                let result = !seed
                seed := result+1
                result
        let division = divF (System.Random(genSeed ()))
        printf "r = %f\n" r
        let fates = Array.init sampleSize (fun seed -> cloneSimulate 230 {symClone with r=r;rng=System.Random(seed)}) 
        let stratTimes = Array.map (fun rho -> (rho,((1.-rho)/rho)*meanDivTime)) rhoAll |> List.ofArray
        let rec likeCalc t acc =
            match t with 
            | [] -> List.rev acc |> Array.ofList
            | (rho,stratTime)::rest ->    printf "rho = %f\n" rho
                                          let sTimer = exponential stratTime (System.Random(genSeed ()))
                                          let sim = Array.map (correctTime 0.<day> division sTimer) fates
                                          let result = likeliHoodCalculation data sim
                                          printf "%f\n" result
                                          likeCalc rest (result::acc)
        likeCalc stratTimes []
    {
    logLikelihood= (Array.map (massSimulation rhoVals) rVals |> transpose )
    r = rVals
    rho= rhoVals
    }

In [37]:
let bins = 5
let expRate = exponential 2.4<day>
let e = timeIt (fun _ -> gridSearch bins bins 2.4<day> expRate lineageData)

r = 0.050000
rho = 0.100000
-2322.100591
rho = 0.300000
-1956.688327
rho = 0.500000
-1747.379427
rho = 0.700000
-1687.995548
rho = 0.900000
-1755.831460
r = 0.150000
rho = 0.100000
-2231.037321
rho = 0.300000
-2207.516538
rho = 0.500000
-1993.467083
rho = 0.700000
-1872.157703
rho = 0.900000
-1783.579068
r = 0.250000
rho = 0.100000
-2125.944832
rho = 0.300000
-2272.470326
rho = 0.500000
-2187.774251
rho = 0.700000
-2045.922114
rho = 0.900000
-1918.702292
r = 0.350000
rho = 0.100000
-2022.223637
rho = 0.300000
-2286.861545
rho = 0.500000
-2257.290315
rho = 0.700000
-2200.936713
rho = 0.900000
-2089.716225
r = 0.450000
rho = 0.100000
-1977.344083
rho = 0.300000
-2204.425711
rho = 0.500000
-2215.762732
rho = 0.700000
-2182.960129
rho = 0.900000
-2046.576876
Wall: 40453.486500ms CPU: 38953.125000ms


In [38]:
Heatmap(
    z = e.logLikelihood,
    x = e.r,
    y = e.rho 
)
|> Chart.Plot
|> Chart.WithWidth 700
|> Chart.WithHeight 700


XPlot.Plotly.PlotlyChart

In [39]:
let bins = 5
let gamRate = gammaDelay 0.5<day> 2.4<day>  8. 
let g = timeIt (fun _ -> gridSearch bins bins 2.4<day> gamRate lineageData)

r = 0.050000
rho = 0.100000
-2430.693441
rho = 0.300000
-2024.163593
rho = 0.500000
-1772.112949
rho = 0.700000
-1694.948464
rho = 0.900000
-1747.286801
r = 0.150000
rho = 0.100000
-2243.196716
rho = 0.300000
-2278.722494
rho = 0.500000
-2090.151599
rho = 0.700000
-1899.604891
rho = 0.900000
-1802.370574
r = 0.250000
rho = 0.100000
-2149.705505
rho = 0.300000
-2356.131410
rho = 0.500000
-2277.493646
rho = 0.700000
-2146.478587
rho = 0.900000
-1988.946678
r = 0.350000
rho = 0.100000
-1983.669425
rho = 0.300000
-2335.120677
rho = 0.500000
-2427.454218
rho = 0.700000
-2297.041978
rho = 0.900000
-2139.409154
r = 0.450000
rho = 0.100000
-2004.539703
rho = 0.300000
-2208.800151
rho = 0.500000
-2534.886455
rho = 0.700000
-2348.688900
rho = 0.900000
-2335.958559
Wall: 48017.949500ms CPU: 46265.625000ms


In [40]:
Heatmap(
    z = g.logLikelihood,
    x = g.r,
    y = g.rho 
)
|> Chart.Plot
|> Chart.WithWidth 700
|> Chart.WithHeight 700


XPlot.Plotly.PlotlyChart

# Histone dilution simulator

![Schematic of histone dilution experiment](histone.png)

The above code allows us to compare models directly with one type of experiment, lineage tracing. Another experiment is capable of giving us both the division rate and the shape of the rate distribution directly. This involves adding a label which is diluted every time the cell divides. If we measure the amount of label in cells that have divided different numbers of times, transform them with a logarithm to the base two, we can plot histograms of the label. This shows that as a population divides, the average label in each cell is roughly halved, and the mean of the distribution is reduced by one.

The label itself is fluorescent so the intensity of the label measured from a microscope image is used as a proxy for the quantity of label in a cell. We can model this dilution process and use the experimental data to search for the best sets of parameters using an approach known as approximate Bayesian computation (ABC).

First we will define a simulator to reproduce this process of dilution, and compare different distributions directly with experimental data. 

The simulator takes an array of initial intensities as an input, a noise function that reflects uneven partitioning of the label on cell division, a random number generator, a division time generator, and an array of the timepoints at which data were collected. The function randomly picks an initial intensity from the array (using the function *randomSample*), and generates new timepoints and associated intensities, by multiplying the previous intensity by 0.5 + the output of the noise function. The initial time is optionally reduced by a factor taken from a uniform random distribution. This is intended to reflect the fact that we do not start the experiment at the start of a division process, but instead part way through. 

Note that in contrast to the lineage tracing we don't take account of cell fate here, instead making a simplifying assumption of one stem cell dividing to give one stem cell (and a differentiated cell that is lost and not measured). 

Finally, we only return the intensities for a single cell at the experimental timepoints (as an array). This is done by going through each of the experimental times and comparing them to the paired simulated times/intensities.



In [41]:
let noNoise =
    fun _ -> 0.
    
let piedrafitaNoise (rng: System.Random) =
    let sqrt12 = 12.**0.5
    fun _ -> (rng.NextDouble()-0.5)*0.06*sqrt12
    //noiseTerms = np.random.uniform(-0.5,0.5,n)*math.sqrt(12)*0.06

let randomSample (rng: System.Random) (a: 'a []) =
    //Randomly select and return an element of the input array
    a.[rng.Next((Array.length a))]

let invertedWeightRandomSample (rng: System.Random) weights (a: 'a []) =
    //Input will be distances-> big distances are worse
    //The weight/probability relationship is therefore assumed to be smaller -> more probable
    //Invert the weights, normalise, and convert to a cdf
    let invertedW = Array.map (fun i -> 1./i) weights
    let total = Array.sum invertedW
    //let prob = Array.map (fun i -> i/total) invertedW
    //printf "Probability\n%A\n" prob
    let cdf = Array.scan (fun totalP i -> totalP+(i/total) ) 0. invertedW
    //printf "CDF\n%A\n" cdf
    fun _ ->
        let num = rng.NextDouble()
        Array.findIndex (fun p -> p>num) cdf
        |> fun i -> a.[i-1]

let weightedRandomSample (rng: System.Random) weights (a: 'a []) =
    //Input will be likelihoods-> big likelihoods are better
    //Take the weights, normalise, and convert to a cdf
    let total = Array.sum weights
    let cdf = Array.scan (fun totalP i -> totalP+(i/total) ) 0. weights
    fun _ ->
        let num = rng.NextDouble()
        Array.findIndex (fun p -> p>num) cdf
        |> fun i -> a.[i-1]

let rec diluteEngine maxtime div noise times dilutions lasttime label =
    if lasttime > maxtime then 
        List.map2 (fun t d -> (t,d)) (lasttime::times) (label::dilutions) |> List.rev
    else
        let dt = div ()
        let lasttime' = lasttime + dt
        let dLabel = 0.5 + (noise ())
        let label' = dLabel*label
        diluteEngine maxtime div noise (lasttime::times) (label::dilutions) lasttime' label'

let rec findObservation timePoints simulation acc prevDilution =
    match timePoints, simulation with
    | [],_ -> List.rev acc //all done
    | _, [] -> failwith "Run out of simulations"
    | t'::otherTimes, (simTime,d)::otherMeasurements -> 
        if simTime > t' then
            //The next timepoint has past- return the *previous* dilution
            let pDil = match prevDilution with
                        | Some(oldD) -> oldD
                        | None -> failwith "Requested timepoint occurs before t=0"
            //How many timepoints have passed? Need to count the timepoints and add the previous label that number of times
            //let acc', remainingTime = peek otherTimes t' (pDil::acc) pDil
            findObservation otherTimes simulation (pDil::acc) prevDilution
        else 
            //timepoint has not arrived, move on
            findObservation timePoints otherMeasurements acc (Some(d))
            
let dilution noise (div: unit -> float<day>) (rng: System.Random) timePoints initialLabel randomiseTime1 = 
    let lastTime = List.max timePoints
    let experiment = if randomiseTime1 then
                        //randomise the initial timepoint
                        let t1 = ( div () ) * rng.NextDouble()
                        let dLabel = (+) 0.5 <| noise ()
                        let label = randomSample rng initialLabel
                        let label' = dLabel* label
                        diluteEngine lastTime div noise [0.<day>] [label] t1 label'
                     else
                         //don't bother
                         diluteEngine lastTime div noise [] [] 0.<day> <| randomSample rng initialLabel
    //for e in experiment do
        //let t,d = e
        //printf "%f\t%f\n" t (Math.Log(d,2.))
    try
        findObservation timePoints experiment [] None |> Array.ofList
    with
        | Failure msg -> failwithf "%s\n%A\n" msg experiment

## Testing the simulators
Here we run some of the functions to explore how they behave and time some of the outputs. 


In [42]:
dilution (noNoise) (gammaFracDelay 0.99 (7.<day>/3.) 8. rng) rng [7.<day>;12.<day>;18.<day>] [|1.|] false |> Array.map (fun x -> Math.Log(x, 2.) )

[|-2.0; -5.0; -7.0|]

In [43]:
let dilutionExperiment noise (div: unit -> float<day>) rng timePoints initialLabel sampleSize randomInit =
        Array.init sampleSize <| fun _ -> dilution noise div rng timePoints initialLabel randomInit

In [77]:
let dtest = timeIt (fun _ -> dilutionExperiment noNoise div rng [7.<day>;12.<day>;18.<day>] [|1.|] 10000 true)

Wall: 42.307200ms CPU: 46.875000ms


## Reading experimental data, and visualising model and experimental results

Using the variable *dataLocation*, set at the start of the tutorial to the location of your notebook, we read some experimental data using FSharp.Data. i0 are the initially measured intensities, whilst the later timepoints are stored in the array of arrays *measurements*. 


In [78]:
let getVal s = if s = "" then nan else float s

let readData (filename: string) count = 
    let raw = FSharp.Data.CsvFile.Load(filename)
    let a = raw.Rows |> Array.ofSeq 
    Array.init (count*(Array.length a)) (fun i -> getVal a.[i/count].[i%count] ) |> Array.filter (fun a ->  not (Double.IsNaN(a)) )

let i0File = dataLocation + "fake_0day.txt"

let i0 = readData i0File 3

let measurements = Array.map (fun (f,c) -> readData f c) [|
                                                            (dataLocation + "fake_7day.txt",3);
                                                            (dataLocation + "fake_12day.txt",3);
                                                            (dataLocation + "fake_18day.txt",3);
                                                            |]
                 |> Array.map (fun m -> Array.map (fun i -> Math.Log(i,2.) ) m)


## Comparing simulations with real data

Here we run 2 sets of simulations of ~1000 cells (roughly the number collected per animal) to visually compare the distributions with the experimental observations. Taking the same rates, we compare an exponential distribution for cell cycle times with a gamma distribution, with a shape of 8 and a fractional delay of 0.5. We then run the simulations and then plot the log2(intensities) from simulations and experimental data against one another using plotly. We use a log2 transformation as it allows us to more easily visualise the label intensity over time- at late timepoints the untransformed graph is highly skewed as the intensity is so low, and the log2 transformation specifically means that each division causes a reduction of label ~= 1 on the transformed graph.

By eye, you can observe that the gamma distribution is more realistic, giving more experimental-like distributions of label. The exponential distributions are broader than the gamma and experimental distributions as some cells divide very quickly, whilst others slowly. In contrast, theres a substantially narrower period of time when cells divide for the gamma distribution, meaning that more cells divide neat the average rate.

In each case we plot all timepoints for the experimental data, exponential simulation, and gamma simulation on a single graph. We then compare individual timepoints. As expected, the day 0 timepoints are identical to the experiment and one another, whilst the later timepoints are most dissimilar.

In [79]:
let rng = System.Random(1)
let mean = 7.<day>/2.974
let sampleSize = 1000
let expDiv = exponential mean rng
let expResult = dilutionExperiment (piedrafitaNoise rng) (expDiv: unit->float<day>) rng [0.<day>;7.<day>;12.<day>;18.<day>] i0 sampleSize true
                |> Array.map (fun sim -> Array.map (fun i -> Math.Log(i,2.)) sim)
let modifier = Array.map (fun (sim:float []) -> sim.[0]) expResult
                |> fun d -> Accord.Statistics.Measures.Mean(d) 
let normalisedExp = Array.map (fun sim -> Array.map (fun i -> i-modifier) sim) expResult |> transpose


In [80]:
let gamDiv = gammaDelay 0.5<day> mean 8. rng
let gamResult = dilutionExperiment (piedrafitaNoise rng) (gamDiv: unit->float<day>) rng [0.<day>;7.<day>;12.<day>;18.<day>] i0 sampleSize true
                |> Array.map (fun sim -> Array.map (fun i -> Math.Log(i,2.)) sim)
let gmodifier = Array.map (fun (sim:float []) -> sim.[0]) expResult
                |> fun d -> Accord.Statistics.Measures.Mean(d) 
let normalisedGam = Array.map (fun sim -> Array.map (fun i -> i-gmodifier) sim) gamResult |> transpose

open System
open System.IO
let gamDiv = gammaDelay 0.52<day> mean 8. rng
let fakeResult = dilutionExperiment (piedrafitaNoise rng) (gamDiv: unit->float<day>) rng [0.<day>;7.4<day>;12.2<day>;17.7<day>] i0 3000 true
                    |> Array.map (fun sim -> Array.map (fun i -> i*(MathNet.Numerics.Distributions.Normal.Sample(1.,0.05) ) ) sim)
let mutable t0 = sprintf "mouse1\tmouse2\tmouse3\n"
for i=0 to ((Array.length fakeResult) - 1) do
    t0 <- t0 + (sprintf "%8.4f" fakeResult.[i].[0])
    t0 <- t0 + if (i+1)%3 <> 0 then sprintf "\t" else sprintf "\n"
File.WriteAllText("fake_0day.txt",t0)

let mutable t7 = sprintf "mouse1\tmouse2\tmouse3\n"
for i=0 to ((Array.length fakeResult) - 1) do
    t7 <- t7 + (sprintf "%8.4f" fakeResult.[i].[1])
    t7 <- t7 + if (i+1)%3 <> 0 then sprintf "\t" else sprintf "\n"
File.WriteAllText("fake_7day.txt",t7)

let mutable t12 = sprintf "mouse1\tmouse2\tmouse3\n"
for i=0 to ((Array.length fakeResult) - 1) do
    t12 <- t12 + (sprintf "%8.4f" fakeResult.[i].[2])
    t12 <- t12 + if (i+1)%3 <> 0 then sprintf "\t" else sprintf "\n"
File.WriteAllText("fake_12day.txt",t12)

let mutable t18 = sprintf "mouse1\tmouse2\tmouse3\n"
for i=0 to ((Array.length fakeResult) - 1) do
    t18 <- t18 + (sprintf "%8.4f" fakeResult.[i].[3])
    t18 <- t18 + if (i+1)%3 <> 0 then sprintf "\t" else sprintf "\n"
File.WriteAllText("fake_18day.txt",t18)

In [81]:
let log2i0 = Array.map (fun i -> Math.Log(i,2.)) i0
let xmodifier = Accord.Statistics.Measures.Mean(log2i0) 
let normi0 = Array.map (fun i -> i - xmodifier) log2i0
let normalisedx = Array.map (fun sim -> Array.map (fun i -> i-xmodifier) sim) measurements //|> transpose

In [82]:
let x0 = Histogram(
            x = normi0,
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let x7 = Histogram(
            x = normalisedx.[0],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let x12 = Histogram(
            x = normalisedx.[1],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let x18 = Histogram(
            x = normalisedx.[2],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Experimental trace"
    )

[x0;x7;x12;x18]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [83]:
let e0 = Histogram(
            x = normalisedExp.[0],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let e7 = Histogram(
            x = normalisedExp.[1],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let e12 = Histogram(
            x = normalisedExp.[2],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let e18 = Histogram(
            x = normalisedExp.[3],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Exponential trace"
    )

[e0;e7;e12;e18]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [84]:
let g0 = Histogram(
            x = normalisedGam.[0],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let g7 = Histogram(
            x = normalisedGam.[1],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let g12 = Histogram(
            x = normalisedGam.[2],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let g18 = Histogram(
            x = normalisedGam.[3],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Gamma trace"
    )

[g0;g7;g12;g18]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [85]:
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Day 0"
    )

[x0;e0;g0]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [86]:
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Day 7"
    )

[x7;e7;g7]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [87]:
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Day 12"
    )

[x12;e12;g12]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

In [88]:
let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Day 18"
    )

[x18;e18;g18]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

XPlot.Plotly.PlotlyChart

### Density plots

Here we define a function to aid the replotting of the histograms as density plots. This gives us a slightly different way to visualise the data (effectively giving us a smoothed curve), but it also introduces the calculation of KDEs using Accord which we use later

In [89]:
let oneDKDE min max binGranularity samples =
    let kernel = new Accord.Statistics.Distributions.DensityKernels.GaussianKernel(1)
    let processedSamples = Array.map (fun i -> [|i|]) samples
    let dist = new Accord.Statistics.Distributions.Multivariate.MultivariateEmpiricalDistribution(kernel, processedSamples)
    let bins = (max-min)/binGranularity |> int |> (+) 1
    let x = Array.init bins (fun i -> float(i)*binGranularity + min )
    let y = Array.map (fun value-> value,dist.ProbabilityDensityFunction([|value|])) x
    let normF = Array.sumBy (fun (_,p) -> p) y
    Array.map (fun (v,e) -> v,e/normF) y
    

In [90]:
let i0Den = oneDKDE -1. 0.4 0.01 normi0
i0Den |> Chart.Line

XPlot.Plotly.PlotlyChart

In [91]:
let density = oneDKDE -18. 0.4 0.01

[normi0;normalisedExp.[0];normalisedGam.[0]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Day 0" ) )
|> Chart.WithLabels ["Experiment"; "Exponential"; "Gamma with delay"]

XPlot.Plotly.PlotlyChart

In [92]:
[normalisedx.[0];normalisedExp.[1];normalisedGam.[1]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Day 7" ) )
|> Chart.WithLabels ["Experiment"; "Exponential"; "Gamma with delay"]

XPlot.Plotly.PlotlyChart

In [93]:
[normalisedx.[1];normalisedExp.[2];normalisedGam.[2]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Day 12" ) )
|> Chart.WithLabels ["Experiment"; "Exponential"; "Gamma with delay"]

XPlot.Plotly.PlotlyChart

In [94]:
[normalisedx.[2];normalisedExp.[3];normalisedGam.[3]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Day 18" ) )
|> Chart.WithLabels ["Experiment"; "Exponential"; "Gamma with delay"]

XPlot.Plotly.PlotlyChart

In [95]:
[normi0;normalisedx.[0];normalisedx.[1];normalisedx.[2]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Experimental observations" ) )
|> Chart.WithLabels ["Day 0"; "Day 7"; "Day 12"; "Day 18"]

XPlot.Plotly.PlotlyChart

In [96]:
[normalisedExp.[0];normalisedExp.[1];normalisedExp.[2];normalisedExp.[3]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Model with exponential distribution" ) )
|> Chart.WithLabels ["Day 0"; "Day 7"; "Day 12"; "Day 18"]

XPlot.Plotly.PlotlyChart

In [97]:
[normalisedGam.[0];normalisedGam.[1];normalisedGam.[2];normalisedGam.[3]]
|> List.map density
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Model with gamma distribution and refractory period" ) )
|> Chart.WithLabels ["Day 0"; "Day 7"; "Day 12"; "Day 18"]

XPlot.Plotly.PlotlyChart

# ABC

The final task of this notebook is to find the best sets of parameters to describe the experimental data using the ABC approach. In the python notebook we were able to use a library pyabc to take care of the details of ABC, but here we have to develop our own approach in the absence of an equivalent. 

We also break one of the rules we've used for this notebook by rewriting a function that is available in the Accord library- the calculation of the two sample KS statistic to compare empirical distributions. We go into why in the related [Optimising F# Functions](OptimisingFSharp.ipynb) notebook, but for here we make three functions available to calculate the statistic- one based on Accord, one using SciPy through pythonnet (*scipyKS*), and the locally defined version (*simplifiedKS*).

Here we implement the ABC-sequential monte carlo algorithm from [Toni et al](https://academic.oup.com/bioinformatics/article/26/1/104/182571). The fundamental process is to generate a set of parameters that generate similar simulations to the experimental data. Initially randomly selected parameters are chosen and the average similarity (or *distance*) to the experimental data is measured. The median distance from the experimental data is then set as a cutoff to define what future parameters are acceptable- if a new simulation gives a higher distance (less similar), the parameters are rejected. To speed up the process of generating parameter sets (known as *particles*), new particles are not randomly sampled, but instead generated by selecting previously accepted particles and perturbing them using a defined noise term. 

This process of perturbing/rejecting particles is looped, reducing the distance cutoff as before until either the number of particle populations has been reached or a defined maximum number of attempts to find a particle has been breached. Different distance functions can change your outputs- here we use a method based on the [KS test](https://en.wikipedia.org/wiki/Kolmogorov%E2%80%93Smirnov_test) and quantile distances.

To summarise this process;

1. Generate initial set of parameters randomly, calculate distances, and calculate the median distance (epsilon)
2. Generate a new set of parameters by selecting from the initial set, making a perturbation to those parameters, and running simulations, rejecting those higher than the previous epsilon
3. Repeat 2, resetting epsilon to the median distance of the new population until you have either calculated enough populations of parameters or until you exceed a maximum number of tries.

To speed up the analysis we also parallelise the calculation of particles through the built-in tools in Array. Due to thread safety we new pass random number generators for each thread, and create a threadsafe bool (*tsBool*) type that can be read/written to by all thread. This allows all threads to be stopped if one reaches its maximum number of attempts.   

Our key outputs here are to generate a scatter plot of accepted parameter sets, and a 2D KDE to show where the highest density of accepted parameters are. This should be able to show how the set of acceptable parameters starts off broad, but focuses down to a smaller set as the distance drops.


## First steps

Initially we define a few functions to specify features of our inference- the search space, parameters for inference, an inerface to the simulator above and associated model formats.

We also define a generic distance function, which takes a summary statistic calculator (another function) as a parameter. We define two of these based on functions available in Accord- the KS statistic and quantile based measurements.

In [98]:
let uniformPrior min max (rng: System.Random) =
    fun _ -> min + (max-min)*rng.NextDouble()
    
type modelRange =
    {
    fracMax : float
    fracMin : float
    shapeMax : float
    shapeMin : float
    }

type modelPriors = 
    {
    fracDelay : unit->float
    log2Shape : unit->float
    }

let rangeToPrior r rng =
    {
    fracDelay = uniformPrior r.fracMin r.fracMax rng
    log2Shape = uniformPrior r.shapeMin r.shapeMax rng
    }

type modelSelection =
    {
    fracDelaySel : float
    log2ShapeSel : float
    }

type modelFixed = 
    {
    mean : float<day>
    initialLabel : float []
    noise : System.Random -> unit -> float
    sampleSize : int
    timePoints : float<day> list
    rng : System.Random
    unknownRanges : modelRange
    randomiseInit : bool
    }

let modelInterface fixPa priors spareRng = 
    let rng = match spareRng with 
              | Some(r) ->r
              | None -> fixPa.rng
    let delay = priors.fracDelay ()
    let log2Shape = priors.log2Shape ()
    let selection = {fracDelaySel=delay;log2ShapeSel=log2Shape}
    let div = gammaFracDelay delay fixPa.mean (2.**log2Shape) rng
    let noise = fixPa.noise rng
    let result = dilutionExperiment noise div rng fixPa.timePoints fixPa.initialLabel fixPa.sampleSize fixPa.randomiseInit
                    |> Array.map (fun m -> Array.map (fun i -> Math.Log(i,2.) ) m)
    (selection,(transpose result))
    
let modelInterfaceParticle fixPa rng p  = 
    let noise = fixPa.noise rng
    let div = gammaFracDelay p.fracDelaySel fixPa.mean (2.**p.log2ShapeSel) rng
    let result = dilutionExperiment noise div rng fixPa.timePoints fixPa.initialLabel fixPa.sampleSize fixPa.randomiseInit
                    |> Array.map (fun m -> Array.map (fun i -> Math.Log(i,2.) ) m)
    (p,(transpose result)) 

let ksSummStat s o =
    Accord.Statistics.Testing.TwoSampleKolmogorovSmirnovTest(s,o).Statistic
    
let quantileSummStat q s o =
    let sq = Accord.Statistics.Measures.Quantiles(s,q)
    let oq = Accord.Statistics.Measures.Quantiles(o,q)
    Array.map2 (fun a b -> abs(a-b)) sq oq
    |> Array.sum

let distance (summStat: 'a [] -> 'a [] -> float) sim measurements = 
    Array.map2 (fun s o -> summStat s o )  sim measurements
    |> Array.sum

type Space = Global | Local of float

type inference = {  populations : int
                    popSize : int
                    maxAttempts : int
                    epsilonMultiplier : float
                    summaryStatistic : float [] -> float [] -> float
                    transition : Space
                    weightPreviousPopulation : bool //Weight previous population by distance to speed up search
                    initialEpsilon : float option
                    }

## Perturbation

How the particles are perturbed can make a difference to both the code efficiency and the final outcome. Here we define two methods for modifying particles based on a Gaussian random walk. 

*randomWalk* takes a set of all particles and calculates a Gaussian KDE using accord. It then calculates the covariance of this KDE, and uses it to bias the Gaussian random walk. The final walk function takes unit and returns an array with the values to update the particle with.

*localRandomWalk* is similar to randomWalk, but instead of looking at the covariance of all particles it calculates the local covariance for each particle based on its nearest neighbours. It calculates the walks once, and then returns an array of two values depending on the particle that is passed to it. The specific functions for each particle are stored in a dictionary, and lookup is based on a string conversion of the input particle.

In [99]:
let randomWalk particles rng =
    let samples = Array.map (fun c -> [|c.fracDelaySel;c.log2ShapeSel|]) particles
    let kernel = new Accord.Statistics.Distributions.DensityKernels.GaussianKernel(2)
    let dist = new Accord.Statistics.Distributions.Multivariate.MultivariateEmpiricalDistribution(kernel, samples)
    let cov = dist.Covariance
    let cho = new Accord.Math.Decompositions.CholeskyDecomposition(cov)
    let L =     cho.LeftTriangularFactor
    //cho.LeftTriangularFactor
    fun _ ->
        let rand = Array.init 2 (fun _ -> MathNet.Numerics.Distributions.Normal.Sample(rng,0.,1.) )
        [| 
            L.[0,0] * rand.[0] + L.[0,1] * rand.[1] ;
            L.[1,0] * rand.[0] + L.[1,1] * rand.[1]
            |]

let getLocalCov number all particle =
    let neighbours = Array.sortBy (fun p -> (pown (p.fracDelaySel-particle.fracDelaySel) 2) + (pown (p.log2ShapeSel-particle.log2ShapeSel) 2) ) all
                     |> fun sortedNeighbours -> Array.init number (fun i -> sortedNeighbours.[i])
    let samples = Array.map (fun c -> [|c.fracDelaySel;c.log2ShapeSel|]) neighbours
    let kernel = new Accord.Statistics.Distributions.DensityKernels.GaussianKernel(2)
    let dist = new Accord.Statistics.Distributions.Multivariate.MultivariateEmpiricalDistribution(kernel, samples)
    let cov = dist.Covariance
    let cho = new Accord.Math.Decompositions.CholeskyDecomposition(cov)
    particle.ToString(), cho.LeftTriangularFactor

let localRandomWalk populationFraction particles rng =
    //Find the nearest neighbours for each particle
    let numberNeighbours = float(Array.length particles) * populationFraction |> int
    let local = getLocalCov numberNeighbours particles
    let environments = Array.map local particles
    let dict = new System.Collections.Generic.Dictionary<string,float[,]>()
    Array.iter (fun i -> dict.Add(i) ) environments
    fun p ->
        match dict.TryGetValue p with
        | false, _ -> failwithf "Particle %s not in original population" p
        | true, L ->    let rand = Array.init 2 (fun _ -> MathNet.Numerics.Distributions.Normal.Sample(rng,0.,1.) )
                        [| 
                        L.[0,0] * rand.[0] + L.[0,1] * rand.[1] ;
                        L.[1,0] * rand.[0] + L.[1,1] * rand.[1]
                        |]

let kdeWeights particles =
    let samples = Array.map (fun c -> [|c.fracDelaySel;c.log2ShapeSel|]) particles
    let kernel = new Accord.Statistics.Distributions.DensityKernels.GaussianKernel(2)
    let dist = new Accord.Statistics.Distributions.Multivariate.MultivariateEmpiricalDistribution(kernel, samples)
    Array.map (fun value -> dist.ProbabilityDensityFunction(value)) samples

let perturb inputRanges (walk: string->float[]) particle =
    let randWalk = walk (particle.ToString())
    let dDelay = 
        let r = randWalk.[0] + particle.fracDelaySel
        //MathNet.Numerics.Distributions.Normal.Sample(particle.fracDelaySel,)
        if r > inputRanges.fracMax then 2.*inputRanges.fracMax-r
        elif r < inputRanges.fracMin then 2.*inputRanges.fracMin-r
        else r
    let dShape = 
        let r = randWalk.[1] + particle.log2ShapeSel
        if r > inputRanges.shapeMax then 2.*inputRanges.shapeMax-r
        elif r < inputRanges.shapeMin then 2.*inputRanges.shapeMin-r
        else r
    {particle with 
        fracDelaySel=dDelay; 
        log2ShapeSel=dShape;
        }

## Safely communicating between threads

One feature we need to include in our code is an elegant way to stop the calculations if one particle search fails. This could be a simple bool ref ultimately that is read/written to by all the threads. This however runs the risk of not being threadsafe, and giving the wrong results. In the best case scenario we might do a few extra calculations if the wrong value is read, but it could also lead to inappropriate early termination. 

To avoide this we define a threadsafe type using the System.Threading library Interlocked functions as below. get and set functions allow us to safelyaccess and modify the value and avoid any thread-related issues.

In [100]:
//Threadsafe bool object for checking other results
type tsBool() =
    let v = ref 0
    member this.contents with 
                                get() = (System.Threading.Interlocked.CompareExchange(v, 1, 1) = 1) 
                                and set(value:bool) = if value then
                                                            ignore( System.Threading.Interlocked.CompareExchange(v, 1, 0) )
                                                        else 
                                                            ignore( System.Threading.Interlocked.CompareExchange(v, 0, 1) )

## Particle searches and the abc functions

The final functions we define do the high level work of the algorithm. *findParticle* takes a particle from a previous population (an array of modelselections), perturbs it using a supplied random walk function, runs a simulation, and compares the output to the observed data. If the distance is below the supplied epsilon, it accepts and returns the particle (wrapped in ''Some''); if not it recursively reruns itself, increasing the number of attempts made. If the number of attempts reaches the user defined maximum it returns none and sets the *failedPrevious* tsBool to true. It also returns none if the *failedPrevious* bool has been set to true by another thread.

The recursive function *abcSMC* calls findParticle to generate a population from the previous population. It creates an array from uniquely seeded random number generators based on the user selected population size, and then through a Parallel.map calls findParticle to generate a list of modelSelection option values. If the tsBool *failMarker* (which is passed to findParticle) has been set, the loop finishes early and the returned array does not include the final partially complete population. Otherwise the new median distance is calculated, and the function rerun until the user selected number of posterior populations have been generated.

Finally, *abc* generates an initial population either without a distance cutoff (so without rejection), or in a similar way to abcSMC. It then calls abcSMC to find the other populations!

In [101]:
let rec findParticle (failedPrevious: tsBool) previousPopulation walk selectFunc eps fixPa infP attempts spareRng=
    if failedPrevious.contents then None else
        let rng = match spareRng with
                    | Some(r) -> r
                    | None -> fixPa.rng
        if attempts = infP.maxAttempts then 
            sprintf "findParticle had too many attempts to finish\n" |> Display
            failedPrevious.contents <- true
            None
        else
            let p,d = selectFunc previousPopulation 
                        //|> perturb fixPa.unknownRanges 0.5 0.5 rng
                        |> perturb fixPa.unknownRanges walk
                        |> modelInterfaceParticle fixPa rng
                        |> (fun (p,sim) -> (p,(distance infP.summaryStatistic sim measurements)) )
            if d < eps then Some(p,d) else findParticle failedPrevious previousPopulation walk selectFunc eps fixPa infP (attempts+1) spareRng

let rec abcSMC measurements populations fixPa eps infP acc eacc =
    if populations = 0 then (List.rev acc) else
        //Create a population from perturbed points in prev generation
        let previous= match acc with
                        | [] -> failwith "abcSMC needs a previous population"
                        | last::_ -> last
        //Parallel population creation. Each with their own rng as System.Random is not thread safe
        let failMarker = tsBool ()
        //Define walk function based on previous population and input selections
        let walk =  match infP.transition with 
                    | Global -> randomWalk previous rng
                    | Local(f) -> localRandomWalk f previous rng
                            
        //Define a function to pick a member of the previous population randomly, with or without weighting by prob from KDE
        //Don't do this on the initial population
        let selectFunc = if infP.weightPreviousPopulation && (1 <> (List.length acc)) then 
                                //precalculate the weighting to avoid doing this on each findParticle run
                                weightedRandomSample rng (kdeWeights previous) previous 
                            else randomSample rng
            
        let popAt' = Array.init infP.popSize (fun _ -> new System.Random(gensym ()))
                    |> Array.Parallel.map (fun rng -> findParticle failMarker previous walk selectFunc eps fixPa infP 0 (Some(rng)) )
                    
        if failMarker.contents then 
            printf "abcSMC- maximum number of attempts exceeded. Stopping now\n"
            List.rev acc
        else
            let pop' = Array.map (fun e -> match e with 
                                            | Some(p) -> p
                                            | _ -> failwith "abcSMC should not end here") popAt'

            let param =  Array.map (fun (p,_) -> p) pop'
            let distances = Array.map (fun (_,d) -> d) pop'
            let eps' = distances
                        |> fun d -> Accord.Statistics.Measures.Median(d)
            sprintf "New episilon = %f" eps' |> Display
            stdout.Flush()
            let acc' = param::acc
            let eacc' = eps'::eacc
            abcSMC measurements (populations-1) fixPa  (infP.epsilonMultiplier*eps') infP acc' eacc'

let abc fixPa measurements inferenceP =
    //Create a single population and calculate the epsilon
    let priors = rangeToPrior fixPa.unknownRanges fixPa.rng
    let initPop,initE = match inferenceP.initialEpsilon with
                        | None -> let p = Array.init inferenceP.popSize (fun _ -> modelInterface fixPa priors None )
                                          |> Array.map (fun (p,sim) -> (p,distance inferenceP.summaryStatistic sim measurements) )
                                  let e = Array.map (fun (_,d) -> d) p
                                          |> fun d -> Accord.Statistics.Measures.Median(d)
                                  p,e
                        | Some(e) ->   let fail = tsBool()
                                       let selectFunc r = let priors = rangeToPrior fixPa.unknownRanges r
                                                          let delay = priors.fracDelay ()
                                                          let log2Shape = priors.log2Shape ()
                                                          fun _  -> {fracDelaySel=delay;log2ShapeSel=log2Shape}
                                       let makePop = fun r -> findParticle fail () (fun _ -> [|0.;0.|]) (selectFunc r) e fixPa inferenceP 0 (Some(r))
                                       let ip =    Array.init (inferenceP.popSize) (fun _ -> new System.Random(gensym ()))
                                                   |> Array.Parallel.map makePop
                                       if fail.contents then 
                                            failwith "Unable to construct an initial population.\nEither increase the acceptance rate or reduce the initial epsilon"
                                       let p =  Array.map (fun e -> match e with 
                                                                    | Some(p) -> p
                                                                    | _ -> failwith "abc should not end here") ip
                                       let e = Array.map (fun (_,d) -> d) p
                                               |> fun d -> Accord.Statistics.Measures.Median(d)
                                       p,e
                                       
    if Array.length initPop <> 0 then                             
        let param = Array.map (fun (p,_) -> p) initPop
        sprintf "Initial episilon = %f" initE |> Display
        //Go into the main loop
        abcSMC measurements inferenceP.populations fixPa initE inferenceP [param] [initE] |> Array.ofList
    else 
        failwith "Unable to construct an initial population. Either increase the acceptance rate or reduce the initial epsilon"

## Local Two-sample KS function

This function was written on the basis of some benchmarks showing that 80% of time spent performing ABC was spent performing the KS test, and that this was slower than the equivalent function in scipy. How this was written is detailed in [another notebook](OptimisingFsharp.ipynb) but the final function itself is given below.

In [102]:
let inline findPosition (someArray: _ []) value =
    let rec find lower upper  =
        if lower=upper then upper else
            let div = (upper-lower)/2 + lower    
            if someArray.[div] > value then find lower div 
            else find (div+1) upper 
    find 0 (Array.length someArray) 
    
let inline cdfDifference a b = 
    let aLen = Array.length a |> float
    let bLen = Array.length b |> float
    let mutable max = 0.
    for i = 0 to ((Array.length b)-1) do
        let diff = findPosition a b.[i] |> fun s -> abs ( float(s)/aLen - float(i+1)/bLen) 
        if diff > max then max <- diff
    max

let inline simplifiedKS s o =
    let data1 = Array.sort s
    let data2 = Array.sort o
    let max1 = cdfDifference data1 data2 
    let max2 = cdfDifference data2 data1
    if max1 > max2 then max1 else max2

## Testing the simulator and distance functions

Here we run through a single set of model simulations with selected parameters to confirm that the functions work correctly together. These outputs can be directly compared with those from the python code, and be found to give similar results, showing that the results are reproducible.

In [103]:
let testParticle = {fracDelaySel=0.5;log2ShapeSel=2.}
let rng = System.Random(1066)
let searchRange = 
    {
        fracMin = 0.
        fracMax = 1.
        shapeMin = 0.
        shapeMax = 6.
    }
 
let fix =
    {
        mean = (7.<day>/3.);
        initialLabel = i0;
        noise = piedrafitaNoise 
        sampleSize = 1000
        timePoints = [7.<day>;12.<day>;18.<day>]
        rng = rng
        unknownRanges=searchRange
        randomiseInit = true
    }
let _,sim = modelInterfaceParticle fix rng testParticle
printf "d = %f\n" <| distance simplifiedKS sim measurements
for i in [0;1;2] do
    printf "d%d = %f\n" i <| simplifiedKS sim.[i] measurements.[i]

d = 0.218000
d0 = 0.074000
d1 = 0.043333
d2 = 0.100667


In [104]:
measurements.[0]

[|4.277754195; 4.597328551; 3.537867564; 4.101759316; 4.060090629; 3.770131311;
  2.851878941; 3.465399883; 3.950459082; 3.020253271; 4.079275698; 5.614809946;
  3.504798335; 4.696667136; 3.852418397; 4.098048932; 4.606234929; 5.89963486;
  4.314580525; 4.722799336; 2.852877774; 3.86811384; 3.914908892; 2.888675069;
  2.232138837; 4.168449492; 4.604071324; 4.782025823; 3.088463894; 4.881762492;
  3.177646763; 3.220314475; 5.64776636; 4.49999254; 5.111832587; 3.426224493;
  4.784163685; 5.552918042; 3.730661691; 5.738084151; 3.214575577; 4.638653116;
  5.69090592; 4.535505567; 5.413397756; 2.986811375; 4.377685999; 4.324155339;
  3.154080881; 4.818845449; 4.423598339; 3.07522455; 4.428698507; 3.587208951;
  4.754823381; 3.01834931; 5.070213274; 2.610959856; 4.057840137; 3.673115407;
  4.042477998; 4.40819555; 4.68290472; 3.880597374; 2.835236913; 3.582026034;
  3.738346314; 3.355382813; 2.812005263; 3.904638234; 4.026454833; 4.65899404;
  3.703643381; 3.680673172; 2.909369899; 4.4024425

In [105]:
sim.[0]

[|3.644510815; 4.359097919; 5.260095149; 4.774926791; 5.483308033; 4.235110848;
  4.040985557; 4.426897809; 4.355367341; 4.400203055; 5.478305301; 4.728037651;
  4.415627387; 4.157069082; 3.63288373; 3.089696946; 4.329183672; 4.623721004;
  5.809303071; 3.234183116; 4.834811482; 4.600845969; 4.032433411; 4.902290876;
  4.96420902; 2.950879467; 5.257788; 4.739981068; 4.799546847; 3.928595464;
  3.834889517; 4.731422368; 2.609769562; 4.613911106; 3.421954955; 4.026460718;
  3.509051157; 4.102376784; 4.341887678; 4.353418522; 4.086683388; 4.322023772;
  3.997437422; 3.551626899; 4.287453489; 4.462832038; 4.188185397; 4.57749777;
  4.351312682; 3.86106237; 3.74215823; 4.216579565; 3.424438016; 4.345090373;
  4.193976609; 4.074702742; 3.946160231; 4.557291326; 4.128911646; 4.698781423;
  4.104082284; 3.773647803; 4.787457454; 5.515576024; 4.306724161; 4.881745506;
  3.626659772; 2.995121857; 3.967419848; 4.36892786; 5.559956023; 3.89407245;
  4.661461699; 4.759375405; 5.30957037; 4.76664899

In [106]:
[
Histogram(
            x = log2i0,
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            );
Histogram(
            x = sim.[0],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            );
Histogram(
            x = measurements.[0],
            opacity = 0.75,
            histnorm = "probability",
            autobinx = true
            )]
|> Chart.Plot

XPlot.Plotly.PlotlyChart

## ABC search for acceptable parameters

Below we search for the best fitting parameters with a fractional delay of zero to one, and a shape from 1 to 64. 

In [107]:
let rng = System.Random(1066)
let searchRange = 
    {
        fracMin = 0.
        fracMax = 1.
        shapeMin = 0.
        shapeMax = 6.
    }
 
let fixedParameters =
    {
        mean = (7.<day>/3.);
        initialLabel = i0;
        noise = piedrafitaNoise 
        sampleSize = 1000
        timePoints = [7.<day>;12.<day>;18.<day>]
        rng = rng
        unknownRanges=searchRange
        randomiseInit = true
    }
let inp =
    { 
        populations = 5;
        popSize = 1000; 
        maxAttempts = 10000;
        epsilonMultiplier = 0.98 
        summaryStatistic = simplifiedKS
        transition = Global 
        weightPreviousPopulation = false
        initialEpsilon = None
    }
let infer = timeIt (fun _ -> abc fixedParameters measurements inp)

"Initial episilon = 0.392833"

"New episilon = 0.296333"

"New episilon = 0.237500"

"New episilon = 0.213333"

"New episilon = 0.199333"

"New episilon = 0.188333"

Wall: 50016.563600ms CPU: 122781.250000ms


## Plotting the outputs

We can manually examine the particles in the infer array to ensure there are no major errors, but plotting is necessary to interpret the results. 

Using plotly, we can generate a scatter graph and a heatmap of the particles, which shows that the initial population (infer.[0]) covers most of parameter space, whilst the last population (found using Array.last) suggests that the true parameters have a short delay and a shape term of ~8.

Similar to our density plots above, we can use a KDE to plot a smoothed heatmap of our data. Here we define a function *kdePlot* which uses Accord and plotly to visualise the data.

Finally, we repeat the analysis with a different distance function based on quantile distances. This gives similar results, but the distance function is less able to discriminate between shape and delay parameters. This suggests instead a roughly linear relationship between the two of them rather than a single peak observed using a KS based distance.

In [108]:
infer.[0]

[|{fracDelaySel = 0.6316281956;
   log2ShapeSel = 3.609430264;}; {fracDelaySel = 0.005112648944;
                                  log2ShapeSel = 2.24741531;};
  {fracDelaySel = 0.4664080825;
   log2ShapeSel = 0.4026697271;}; {fracDelaySel = 0.2945086804;
                                   log2ShapeSel = 4.241961272;};
  {fracDelaySel = 0.4806896273;
   log2ShapeSel = 5.682276207;}; {fracDelaySel = 0.7392639945;
                                  log2ShapeSel = 1.075450955;};
  {fracDelaySel = 0.6896833236;
   log2ShapeSel = 0.6560957649;}; {fracDelaySel = 0.03898207845;
                                   log2ShapeSel = 0.6037374132;};
  {fracDelaySel = 0.910670368;
   log2ShapeSel = 5.673087439;}; {fracDelaySel = 0.2106987202;
                                  log2ShapeSel = 0.8489698865;};
  {fracDelaySel = 0.5286039824;
   log2ShapeSel = 5.724074615;}; {fracDelaySel = 0.1097279061;
                                  log2ShapeSel = 4.645128168;};
  {fracDelaySel = 0.7592892799;
   log2

In [109]:
let r = Array.last infer
r


[|{fracDelaySel = 0.1062895508;
   log2ShapeSel = 3.147945942;}; {fracDelaySel = 0.3636000617;
                                  log2ShapeSel = 2.285694133;};
  {fracDelaySel = 0.4604521913;
   log2ShapeSel = 1.93418646;}; {fracDelaySel = 0.0205477864;
                                 log2ShapeSel = 3.382701076;};
  {fracDelaySel = 0.04649692946;
   log2ShapeSel = 3.573663606;}; {fracDelaySel = 0.03571019933;
                                  log2ShapeSel = 3.414556898;};
  {fracDelaySel = 0.0144735101;
   log2ShapeSel = 3.487671016;}; {fracDelaySel = 0.4276456233;
                                  log2ShapeSel = 1.847922313;};
  {fracDelaySel = 0.469903491;
   log2ShapeSel = 1.910512198;}; {fracDelaySel = 0.5258000619;
                                  log2ShapeSel = 1.470161803;};
  {fracDelaySel = 0.2377716855;
   log2ShapeSel = 2.287810224;}; {fracDelaySel = 0.08962978614;
                                  log2ShapeSel = 3.292996096;};
  {fracDelaySel = 0.2037501808;
   log2ShapeSe

In [110]:

let points = Scatter(
                        x = Array.map (fun c -> c.fracDelaySel) r,
                        y = Array.map (fun c -> c.log2ShapeSel) r,
                        mode = "markers"
                    )
points |> Chart.Plot

XPlot.Plotly.PlotlyChart

In [111]:
Histogram2d(
    x = Array.map (fun c -> c.fracDelaySel) r,
    y = Array.map (fun c -> c.log2ShapeSel) r,
    histnorm = "probability",
    autobinx = false,
    xbins =
        Xbins(
            start = 0.,
            ``end`` = 1.,
            size = 0.1
        ),
    autobiny = false,
    ybins =
        Ybins(
            start = 0.,
            ``end`` = 6.,
            size = 0.5
        )
)
|> Chart.Plot


XPlot.Plotly.PlotlyChart

In [112]:
let kdePlot ranges particles  =
    let samples = Array.map (fun c -> [|c.fracDelaySel;c.log2ShapeSel|]) particles
    let kernel = new Accord.Statistics.Distributions.DensityKernels.GaussianKernel(2)
    let dist = new Accord.Statistics.Distributions.Multivariate.MultivariateEmpiricalDistribution(kernel, samples)
    let granularity = 100
    let fGran = float(granularity)
    let translateDelay x =
        let r = ranges.fracMin + float(x)/fGran*(ranges.fracMax - ranges.fracMin) + (ranges.fracMax - ranges.fracMin)/(2.*fGran)
        //printf "D:\t%f\t" r
        r
    let translateShape y =
        let r = ranges.shapeMin + float(y)/fGran*(ranges.shapeMax - ranges.shapeMin) + (ranges.shapeMax - ranges.shapeMin)/(2.*fGran)
        //printf "S:\t%f\n" r
        r
    let hm = Array.init granularity (fun x -> 
                Array.init granularity (fun y -> 
                    dist.ProbabilityDensityFunction([|(translateDelay x);(translateShape y)|]) ) )
    Heatmap(
        z = hm,
        x = (List.init granularity translateShape ),
        y = (List.init granularity translateDelay ) 
    )
    |> Chart.Plot
    |> Chart.WithWidth 700
    |> Chart.WithHeight 700


In [113]:
kdePlot searchRange infer.[0]

XPlot.Plotly.PlotlyChart

In [114]:
Array.map (fun p -> p.log2ShapeSel) infer.[0] 
|> oneDKDE 0. 6. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Log2(Shape), Initial Population" ) )


XPlot.Plotly.PlotlyChart

In [115]:
Array.map (fun p -> p.fracDelaySel) infer.[0] 
|> oneDKDE 0. 1. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Fractional Delay, Initial Population" ) )


XPlot.Plotly.PlotlyChart

In [116]:
kdePlot searchRange (Array.last infer )

XPlot.Plotly.PlotlyChart

In [117]:
Array.map (fun p -> p.log2ShapeSel) <| Array.last infer
|> oneDKDE 0. 6. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Log2(Shape), Final Population" ) )


XPlot.Plotly.PlotlyChart

In [118]:
Array.map (fun p -> p.fracDelaySel) <| Array.last infer
|> oneDKDE 0. 1. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Fractional Delay, Final Population" ) )


XPlot.Plotly.PlotlyChart

## Testing with a quantile based distance function

In [119]:
let inp = //"works"=will not take forever
    { 
        populations = 4; //4 works
        popSize = 200; //50 works
        maxAttempts = 10000;
        epsilonMultiplier = 0.98 //0.99 works
        summaryStatistic = quantileSummStat [|0.025;0.25;0.5;0.75;0.975|]
        transition = Global
        weightPreviousPopulation = false
        initialEpsilon = None
    }
let inferQ = timeIt (fun _ -> abc fixedParameters measurements inp)

"Initial episilon = 4.204644"

"New episilon = 2.609556"

"New episilon = 2.096938"

"New episilon = 1.850559"

"New episilon = 1.723482"

Wall: 6796.655000ms CPU: 15187.500000ms


In [120]:
kdePlot searchRange inferQ.[0]

XPlot.Plotly.PlotlyChart

In [121]:
let points = Scatter(
                        x = Array.map (fun c -> c.fracDelaySel) inferQ.[0],
                        y = Array.map (fun c -> c.log2ShapeSel) inferQ.[0],
                        mode = "markers"
                    )
points |> Chart.Plot

XPlot.Plotly.PlotlyChart

In [122]:
inferQ.[0]

[|{fracDelaySel = 0.6292365704;
   log2ShapeSel = 1.712860516;}; {fracDelaySel = 0.6765892136;
                                  log2ShapeSel = 2.383817471;};
  {fracDelaySel = 0.8145678396;
   log2ShapeSel = 1.161774659;}; {fracDelaySel = 0.3840664022;
                                  log2ShapeSel = 4.844582366;};
  {fracDelaySel = 0.5772643274;
   log2ShapeSel = 1.337647437;}; {fracDelaySel = 0.09007611223;
                                  log2ShapeSel = 3.595158657;};
  {fracDelaySel = 0.2559312742;
   log2ShapeSel = 3.353956862;}; {fracDelaySel = 0.429420036;
                                  log2ShapeSel = 1.264837099;};
  {fracDelaySel = 0.6974526521;
   log2ShapeSel = 2.013601087;}; {fracDelaySel = 0.4070845928;
                                  log2ShapeSel = 4.763997257;};
  {fracDelaySel = 0.3972701483;
   log2ShapeSel = 1.32955693;}; {fracDelaySel = 0.2867588598;
                                 log2ShapeSel = 2.658354519;};
  {fracDelaySel = 0.7746188956;
   log2ShapeSel 

In [123]:
kdePlot searchRange (Array.last inferQ )

XPlot.Plotly.PlotlyChart

In [124]:

let points = Scatter(
                        x = Array.map (fun c -> c.fracDelaySel) (Array.last inferQ),
                        y = Array.map (fun c -> c.log2ShapeSel) (Array.last inferQ),
                        mode = "markers"
                    )
points |> Chart.Plot

XPlot.Plotly.PlotlyChart

In [125]:
Histogram2d(
    x = Array.map (fun c -> c.fracDelaySel) (Array.last inferQ),
    y = Array.map (fun c -> c.log2ShapeSel) (Array.last inferQ),
    histnorm = "probability",
    autobinx = false,
    xbins =
        Xbins(
            start = 0.,
            ``end`` = 1.,
            size = 0.1
        ),
    autobiny = false,
    ybins =
        Ybins(
            start = 0.,
            ``end`` = 6.,
            size = 0.5
        )
)
|> Chart.Plot

XPlot.Plotly.PlotlyChart

In [126]:
Array.map (fun p -> p.fracDelaySel) <| Array.last inferQ
|> oneDKDE 0. 1. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Fractional Delay, Final Population" ) )


XPlot.Plotly.PlotlyChart

In [127]:
Array.map (fun p -> p.log2ShapeSel) <| Array.last inferQ
|> oneDKDE 0. 6. 0.01
|> Chart.Line
|> Chart.WithOptions (Options ( title = "Fractional Delay, Final Population" ) )


XPlot.Plotly.PlotlyChart

# Conclusions

We've shown how you can build simulators, visualise their results, and use them to analyse experimental data. This has been achieved using available libraries and tools to plot the results in the notebook. Each function can be rerun with altered parameters and explored in the notebook, or even rewritten to analyse your own data!